In [ ]:
import networkx as nx
%pylab inline
import time
from collections import defaultdict
import pickle

In [ ]:
'''
Because of the big amount of data, I decide to save less data of opinion profiles and to save only the number of 
nodes in a comunity and not who belongs to a certain comunity

Simulation parameters:

n = number of agents
m = number of links added at each step from the new node (parameter for Barabasi Albert model)

N = number of cycles

threshold = tollerance
mu = Deffuanf model parameter. It quantifies the change of opinion when two agents interact
w = probability of rewiring


Outputs:

G = the final network
opinionProfileS = list of lists: opinionProfileS[i][j] is the opinion of agent j at step i * 1000
num_members = list: num_members[i] is a the number of agents in the i-th largest comunity

'''

def opinionDynamics(n, m, N, threshold, mu, w):

    # Create a barabasi albert network with n nodes and m new links for each new node
    G = nx.barabasi_albert_graph(n, m)    

    # Each node has an opinion in range [0,1] 
    for m in G.nodes():
        G.node[m]['Opinion'] = random.random()
    
    # opinionProfile is a list with the opinion of all agents, while opinionProfiles is a list of opinion profile list
    # opinionProfileS[i][j] is the opinion of agent j after i step of the simulation

    opinionProfile = [None] * len(G.nodes())
    
    opinionProfileS = [None] * (int(N / 1000) + 1)
        
    opinionProfile = [G.node[i]["Opinion"] for i in range(len(G.nodes()))]
   
    opinionProfileS[0] = opinionProfile 
    

    # Here the iteration start

    for m in range(N+1):

        # Select one node i randomply and one of its neighbor j
        i = random.randint(0, len(G.nodes()) - 1)

        if bool(list(nx.all_neighbors(G,i))) : # if i has no neighbors the statement returns false

            j = random.choice(list(nx.all_neighbors(G,i)))

            if random.random() > w : # they interact

                if abs(G.node[i]['Opinion'] - G.node[j]['Opinion']) < threshold :

                    op = (G.node[i]['Opinion'] + G.node[j]['Opinion']) * mu
                    
                    # i and j change opinion
                    G.node[i]['Opinion'] = op
                    G.node[j]['Opinion'] = op
                    opinionProfile[i] = op
                    opinionProfile[j] = op                                          
                
                opinionProfile = opinionProfile.copy()
                
                #update of opinionProfileS with the new opinionProfile, one of every 1000 cycle
                if (m % 1000) == 0:
                
                    opinionProfileS[int(m / 1000)] = opinionProfile
                
            else: # i tries to rewire the link

                if abs(G.node[i]['Opinion'] - G.node[j]['Opinion']) >= threshold :

                    G.add_edge(i, random.choice(list(nx.non_neighbors(G,i))))
                    G.remove_edge(i,j)
            
                #update of opinionProfileS with the same opinionProfile because here nobody change opinion, one of1000 cycle
                if (m % 1000) == 0:
                
                    opinionProfileS[int(m / 1000)] = opinionProfile
                
        else: # it runs if i has no neighbors

            #update of opinionProfileS with the same opinionProfile because here nobody change opinion, one of 1000 cycle
            if (m % 1000) == 0:
                
                    opinionProfileS[int(m / 1000)] = opinionProfile
            
# Here is the code to detect comunities. At the end of the simulation, i search links connecting two nodes with
# distant opinions and i delete that. This ensures me to count the real number of comunities.
# I will do this operation with a copy of the original network.
# After that, i remove all nodes with no links
# I want to save only how many nodes a component has

    H = G.copy()
            
    for i in list(H.edges()):
    
        # if the opinion difference is not bounded, the link is broken
        if abs(H.node[i[0]]['Opinion'] - H.node[i[1]]['Opinion']) > threshold :

            H.remove_edge(i[0], i[1])

        # nodes with no links are removed
        H.remove_nodes_from(list(nx.isolates(H)))
        
# I define the connectend_comunity as the list in which the j-th element contains nodes of the j-th largest component
    comunities = list(sorted(nx.connected_components(H))) 
    
    num_members = [None] * len(comunities) 
    
    for i in range(len(comunities)):
        num_members[i] = len(comunities[i])

    num_members = sorted(num_members, reverse = True)

    return G, opinionProfileS, num_members




## GRAPH ##

def plot_opinion_profiles(opinionProfileS):

    plt.figure(figsize=(10,7))  # Generate a white plot of choosen size

    y = []
    
    for mm in range(len(opinionProfileS[0])):

        x = list(range(len(opinionProfileS)))



        y = [opinionProfileS[k][mm] for k in range(len(opinionProfileS))]

        
        
        plt.plot(x,y,'-')    # Replot the opinions af all agents in function of time


    plt.ylim((0,1))

    plt.xlabel('$k_{in}$', fontsize=18)
    plt.ylabel('$P(k_{in})$', fontsize=18)

    plt.xticks(fontsize=14)
    plt.yticks(fontsize=14)


    plt.show()





In [ ]:
# This is a test simulation

start_time = time.time()

n, m = 1000, 5
N = 150000
threshold, mu = 0.4, 0.5
w = 0.4

G, opinion_profiles,number_comunities = opinionDynamics(n, m, N, threshold, mu, w)


print("---Time for running %s seconds ---" % (time.time() - start_time))

start_time = time.time()



plot_opinion_profiles(opinion_profiles)


print("--- Time for plotting %s seconds ---" % (time.time() - start_time))
print("Number of comunities" ,len(number_comunities) )


# Inizio simulazione

In [ ]:
# Make a list with 100 tollerance values in interval [0.05, 0.40]

threshold = linspace(0.05, 0.4, 100)
threshold = list(threshold.round(decimals = 3))

threshold

In [ ]:
# The experiment. I do 100 run for each tollerance value

start_time = time.time()

n, m = 1000, 5
N = 150000
mu = 0.5
w = 0.4

Nn = 100 # number of run for each tollerance value

#creo tre dizionari di liste, uno per ogni output del singolo run
#la chiave del dizionario sarà il valore della threshold e come valori ci sono gli output delle run: il j-esimo
# elemento della lista nel valore della chiave è la quantità output della j-esima run

# Create three dictionary of lists, one for each output. The keys of the dictionaries are values of the tollerance
# and for each key there are 100 elements, one for each output.
# For example: experiment_num_comunities[epsilon1][i] is a list with the number of agents in each comunity in
# decreasing order for the i-th run with tollerance value of epsilon1

#experiment_G = defaultdict(list)  
experiment_opinion_profiles = defaultdict(list)
experiment_num_comunities = defaultdict(list)

for epsilon in threshold:
    
    # Take control of simulation
    
    if epsilon == threshold[10]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[20]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[30]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[40]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[50]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[60]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[70]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[80]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[90]:
        
        print ("Running for threshold= ", epsilon)
        
    elif epsilon == threshold[-1]:
        
        print ("Running for threshold= ", epsilon)
    
    
    
    #experiment_G[epsilon] = [None] * Nn 
    experiment_opinion_profiles[epsilon] = [None] * Nn 
    experiment_num_comunities[epsilon] = [None] * Nn 

    
    for mm in range(Nn):
        
        experiment_G, opinion_profiles,number_comunities = opinionDynamics(n, m, N, epsilon, mu, w)
        
        #experiment_G[epsilon].append(experiment_G)  #epsilon è la chiave, mm è l'elemento mm-esimo della lista dei valori
        experiment_opinion_profiles[epsilon][mm] = opinion_profiles
        experiment_num_comunities[epsilon][mm] = number_comunities
        
print("--- Time for running %s seconds ---" % (time.time() - start_time))
        


## Save and load file

In [ ]:
# save output in a file
pickle.dump( experiment_opinion_profiles, open( "experiment_opinion_profiles_prova.p", "wb" ) )

In [ ]:
# save output in a file
pickle.dump( experiment_num_comunities, open( "experiment_num_comunities_prova.p", "wb" ) )

# Data Analysis

# Number of comunities Vs tollerance

In [ ]:
# Create a dictionary of lists. Keys are tollerance value while values are lists of two elements for each key with
# mean number of comunities and relative standard deviation for a tollerance value

number_of_comunities2 = defaultdict(list)

for epsilon in threshold:
    
    # If the file is modified by the second part of the analysis that add a 0 element to each list with just one
    # comunity, we need to delete this zero element. Otherwise we will never have consensus with just one comunity
    # but we will see always two comunities, one with all agents and the other with no agents
    
    for i in range(len(experiment_num_comunities[epsilon])):
        
        if len(experiment_num_comunities[epsilon][i]) > 1 :
    
            if experiment_num_comunities[epsilon][i][1] == 0:

                del(experiment_num_comunities[epsilon][i][1])
    
    number_of_comunities = [len(experiment_num_comunities[epsilon][i]) for i in range(len(experiment_num_comunities[epsilon]))]
    mean_number_of_comunities = mean(number_of_comunities)
    stdev_number_of_comunities = std(number_of_comunities)
    num_comunities = [mean_number_of_comunities, stdev_number_of_comunities]
    number_of_comunities2[epsilon].append(num_comunities)
    

number_of_comunities2

In [ ]:
# Create lists for plot:
#num_com is the mean number of comunities
#num_com_err is the standard deviation

num_com = [None] * len(number_of_comunities2.values())
num_com_err = [None] * len(number_of_comunities2.values())

for i in range(len(number_of_comunities2.values())):
    num_com[i] = list(number_of_comunities2.values())[i][0][0] 
    num_com_err[i] = list(number_of_comunities2.values())[i][0][1] 
      
print(num_com)

In [ ]:
list(number_of_comunities2.keys())

In [ ]:
# Plot of the number of comunities Vs tollerance value in log-log scale
# Replot with the function y=1/(2epsilon)

y = list(number_of_comunities2.keys())
z = []
ones = []
twos = []

for i in range(len(y)):
    z.append(0.5 * y[i] ** -1)
    ones.append(1)
    twos.append(2)

plt.figure(figsize=(10,7)) 

matplotlib.pyplot.loglog(number_of_comunities2.keys(), num_com, ls = 'dotted')
#matplotlib.pyplot.errorbar(number_of_comunities2.keys(), num_com , yerr = num_com_err) #plot with standard deviation
matplotlib.pyplot.loglog(number_of_comunities2.keys(), z) 
matplotlib.pyplot.loglog(number_of_comunities2.keys(), ones)
matplotlib.pyplot.loglog(number_of_comunities2.keys(), twos) 

plt.xlabel('$log \, \epsilon$', fontsize=18)
plt.ylabel('$log \, (Number\, of\, comunities)$', fontsize=18)



# Mean number of agents in giant and second giant comunity Vs tollerance

In [ ]:
# Create two dictionary of lists. Keys are tollerance value and values are the mean number of agents in giant and 
# second giant component with relative standard deviation

nodes_in_giant_component2 = defaultdict(list)
nodes_in_second_giant_component2 = defaultdict(list)

for epsilon in threshold:

    number_in_giant_component = [experiment_num_comunities[epsilon][i][0] for i in range(len(experiment_num_comunities[epsilon]))]
    mean_nodes_in_giant_component = mean(number_in_giant_component)
    stdev_nodes_in_giant_component = std(number_in_giant_component)
    nodes_in_giant_component = [mean_nodes_in_giant_component, stdev_nodes_in_giant_component]
    nodes_in_giant_component2[epsilon].append(nodes_in_giant_component)
    
    # If there is consensus, there is no second component. To take account of this I add a value of 0 that says that 
    # the second largest component has zero agents
       
    for i in range(len(experiment_num_comunities[epsilon])):
        
        if len(experiment_num_comunities[epsilon][i]) == 1:
            
            experiment_num_comunities[epsilon][i].append(0)
    
    number_in_second_giant_component = [experiment_num_comunities[epsilon][i][1] for i in range(len(experiment_num_comunities[epsilon]))]
    mean_nodes_in_second_giant_component = mean(number_in_second_giant_component)
    stdev_nodes_in_second_giant_component = std(number_in_second_giant_component)
    nodes_in_second_giant_component = [mean_nodes_in_second_giant_component, stdev_nodes_in_second_giant_component]
    nodes_in_second_giant_component2[epsilon].append(nodes_in_second_giant_component)
    


In [ ]:
# Lists for plot:
#num e num2 are the mean numbers of agents in the largest and secon largest comunity
#num_err e num2_err are the standard deviation of the previous quantity

num = [None] * len(nodes_in_giant_component2.values())
num_err = [None] * len(nodes_in_giant_component2.values())

num2 = [None] * len(nodes_in_giant_component2.values())
num2_err = [None] * len(nodes_in_giant_component2.values())

for i in range(len(nodes_in_giant_component2.values())):
    num[i] = list(nodes_in_giant_component2.values())[i][0][0] / n
    num_err[i] = list(nodes_in_giant_component2.values())[i][0][1] /n 
    
    num2[i] = list(nodes_in_second_giant_component2.values())[i][0][0] / n
    num2_err[i] = list(nodes_in_second_giant_component2.values())[i][0][1] / n
    
#print(num, num2)


In [ ]:
# Plot the mean numbers of agents in the largest and secon largest comunity in function of the tollerance
# with relative error bar

plt.figure(figsize=(10,7)) 

matplotlib.pyplot.errorbar(nodes_in_giant_component2.keys(), num , yerr = num_err)
matplotlib.pyplot.errorbar(nodes_in_second_giant_component2.keys(), num2 , yerr = num2_err)

plt.xlabel('$\epsilon$', fontsize=18)
plt.ylabel('Relative number of agents ', fontsize=18)
